# Amazon SageMaker RL상에서 stable baseline으로 Roboschool 시뮬레이션 훈련
---

## 소개

Roboschool은 로봇 시스템에 대한 RL 정책을 훈련시키는 데 일반적으로 사용되는 [오픈 소스](https://github.com/openai/roboschool/tree/master/roboschool) 물리 시뮬레이터입니다. Roboschool은 다양한 로봇 문제에 해당하는 [다양한](https://github.com/openai/roboschool/blob/master/roboschool/__init__.py) gym 환경들을 제공합니다. 그 중 하나는 **HalfCheetah** 입니다. 이것은 다리가 두 개인 로봇으로, 수직 면(vertical plane)으로 제한되어 있어 앞,뒤로만 움직일 수 있습니다.


이 노트북 예제에서는 **HalfCheetah**가 걷는 법을 배우며, [OpenAI Baselines](https://github.com/openai/baselines) 를 기반으로 한 개선된 RL (Reinforcement Learning) 알고리즘의 구현체인 [stable-baselines](https://stable-baselines.readthedocs.io/en/master/) 를 사용합니다.

In [1]:
roboschool_problem = 'half-cheetah'

## 전제 조건(Pre-requisites)

### 라이브러리 임포트

시작하기 위해, 필요한 Python 라이브러리를 가져와서 권한 및 구성을 위한 몇 가지 전제 조건으로 환경을 설정합니다.

In [2]:
import sagemaker
import boto3
import sys
import os
import subprocess
from IPython.display import HTML
import time
from time import gmtime, strftime
sys.path.append("common")
from misc import get_execution_role, wait_for_s3_object
from docker_utils import build_and_push_docker_image
from sagemaker.rl import RLEstimator

### S3 버킷 설정

체크포인트(checkpoint) 및 메타데이터에 사용하려는 S3 버킷에 대한 연결 및 인증을 설정합니다.

In [3]:
sage_session = sagemaker.session.Session()
s3_bucket = sage_session.default_bucket()  
s3_output_path = 's3://{}/'.format(s3_bucket)
print("S3 bucket path: {}".format(s3_output_path))

S3 bucket path: s3://sagemaker-us-west-2-143656149352/


### 변수 설정

훈련 작업의 작업 접두사(job prefix)와 *컨테이너의 이미지 경로(BYOC 인 경우에만)와 같은 변수*를 정의합니다.

In [4]:
# create a descriptive job name 
job_name_prefix = 'rl-roboschool-'+roboschool_problem

### 훈련이 진행되는 위치 구성

SageMaker 노트북 인스턴스 또는 로컬 노트북 인스턴스를 사용하여 RL 훈련 작업을 훈련할 수 있습니다. 로컬 모드는 SageMaker Python SDK를 사용하여 SageMaker에 배포하기 전에 로컬 컨테이너에서 코드를 실행합니다. 이렇게 하면, 익숙한 Python SDK 인터페이스를 사용하면서 반복 테스트 및 디버깅 속도를 높일 수 있습니다. 여러분은 `local_mode = True` 만 설정하면 됩니다.

In [5]:
# run in local_mode on this machine, or as a SageMaker TrainingJob?
local_mode = False

if local_mode:
    instance_type = 'local'
else:
    # If on SageMaker, pick the instance type
    instance_type = "ml.c4.xlarge"

### IAM 역할 생성

SageMaker 노트북 `role = sagemaker.get_execution_role()`을 실행할 때 실행 역할(execution role)을 얻거나 로컬 시스템에서 실행할 때 utils 메소드 `role = get_execution_role()`을 사용하여 실행 역할을 작성하세요.

In [6]:
try:
    role = sagemaker.get_execution_role()
except:
    role = get_execution_role()
print("Using IAM role arn: {}".format(role))

Using IAM role arn: arn:aws:iam::143656149352:role/service-role/AmazonSageMaker-ExecutionRole-20200323T143836


### `로컬` 모드용 도커 설치

로컬 모드에서 작업하려면 도커(docker)가 설치되어 있어야 합니다. 로컬 머신에서 실행할 때는 docker 또는 docker-compose(로컬 CPU 머신의 경우) 및 nvidia-docker(로컬 GPU 머신의 경우)가 설치되어 있는지 확인하세요. 또는, SageMaker 노트북 인스턴스에서 실행할 때 다음 스크립트를 실행하여 관련 패키지들을 설치할 수 있습니다.

참고로, 한 번에 하나의 로컬 노트북만 실행할 수 있습니다.

In [7]:
# only run from SageMaker notebook instance
if local_mode:
    !/bin/bash ./common/setup.sh

## 도커 컨테이너 빌드

Roboschool이 설치된 사용자 정의 도커 컨테이너를 빌드해야 합니다. 컨테이너 빌드 작업은 아래 과정을 거쳐 처리됩니다.

1. 기본 컨테이너 이미지 가져오기
2. Roboschool 및 의존성 패키지 설치
3. stable-baselines 및 OpenMPI와 같은 의존성 패키지 설치
3. 새 컨테이너 이미지를 ECR에 업로드

인터넷 연결이 느린 컴퓨터에서 실행 중인 경우, 이 단계에서 시간이 오래 걸릴 수 있습니다. 노트북 인스턴스가 SageMaker 또는 EC2 인 경우 인스턴스 유형에 따라 3-10 분이 걸립니다.

In [8]:
%%time

cpu_or_gpu = 'gpu' if instance_type.startswith('ml.p') else 'cpu'
repository_short_name = "sagemaker-roboschool-stablebaselines-%s" % cpu_or_gpu
docker_build_args = { 
    'AWS_REGION': boto3.Session().region_name,
}
custom_image_name = build_and_push_docker_image(repository_short_name, build_args=docker_build_args)
print("Using ECR image %s" % custom_image_name)

WARNING! Using --password via the CLI is insecure. Use --password-stdin.
WARNING! Your password will be stored unencrypted in /home/ec2-user/.docker/config.json.
Configure a credential helper to remove this warning. See
https://docs.docker.com/engine/reference/commandline/login/#credentials-store

Login Succeeded
Logged into ECR
Building docker image sagemaker-roboschool-stablebaselines-cpu from Dockerfile
$ docker build -t sagemaker-roboschool-stablebaselines-cpu -f Dockerfile . --build-arg AWS_REGION=us-west-2
Sending build context to Docker daemon   1.67MB
Step 1/41 : ARG AWS_REGION
Step 2/41 : FROM 520713654638.dkr.ecr.${AWS_REGION}.amazonaws.com/sagemaker-rl-tensorflow:coach0.11.0-cpu-py3
coach0.11.0-cpu-py3: Pulling from sagemaker-rl-tensorflow
7b8b6451c85f: Pulling fs layer
ab4d1096d9ba: Pulling fs layer
e6797d1788ac: Pulling fs layer
e25c5c290bde: Pulling fs layer
cd105da4078d: Pulling fs layer
f2c8922a63b9: Pulling fs layer
58eea52eed06: Pulling fs layer
adcd0d06f606: Pulling 

update-alternatives: using /usr/bin/gcc-4.9 to provide /usr/bin/gcc (gcc) in auto mode
Removing intermediate container d258818eb16b
 ---> 20ce5508a306
Step 6/41 : RUN apt-get install -y g++-4.9
 ---> Running in af7f59b655a0
Reading package lists...
Building dependency tree...
Reading state information...
The following additional packages will be installed:
  libstdc++-4.9-dev
Suggested packages:
  g++-4.9-multilib gcc-4.9-doc libstdc++6-4.9-dbg libstdc++-4.9-doc
The following NEW packages will be installed:
  g++-4.9 libstdc++-4.9-dev
0 upgraded, 2 newly installed, 0 to remove and 123 not upgraded.
Need to get 22.1 MB of archives.
After this operation, 45.0 MB of additional disk space will be used.
Get:1 http://archive.ubuntu.com/ubuntu xenial/universe amd64 libstdc++-4.9-dev amd64 4.9.3-13ubuntu2 [1126 kB]
Get:2 http://archive.ubuntu.com/ubuntu xenial/universe amd64 g++-4.9 amd64 4.9.3-13ubuntu2 [21.0 MB]
debconf: delaying package configuration, since apt-utils is not installed
Fetche

 11450K .......... .......... .......... .......... .......... 72%  127M 0s
 11500K .......... .......... .......... .......... .......... 72%  184M 0s
 11550K .......... .......... .......... .......... .......... 72%  199M 0s
 11600K .......... .......... .......... .......... .......... 73%  159M 0s
 11650K .......... .......... .......... .......... .......... 73%  168M 0s
 11700K .......... .......... .......... .......... .......... 73%  146M 0s
 11750K .......... .......... .......... .......... .......... 73%  158M 0s
 11800K .......... .......... .......... .......... .......... 74%  234M 0s
 11850K .......... .......... .......... .......... .......... 74%  200M 0s
 11900K .......... .......... .......... .......... .......... 74%  243M 0s
 11950K .......... .......... .......... .......... .......... 75%  228M 0s
 12000K .......... .......... .......... .......... .......... 75%  240M 0s
 12050K .......... .......... .......... .......... .......... 75%  212M 0s
 12100K ....

checking for perl... perl

== Configuring Open MPI

*** Startup tests
checking build system type... x86_64-unknown-linux-gnu
checking host system type... x86_64-unknown-linux-gnu
checking target system type... x86_64-unknown-linux-gnu
checking for gcc... gcc
checking whether the C compiler works... yes
checking for C compiler default output file name... a.out
checking for suffix of executables... 
checking whether we are cross compiling... no
checking for suffix of object files... o
checking whether we are using the GNU C compiler... yes
checking whether gcc accepts -g... yes
checking for gcc option to accept ISO C89... none needed
checking whether gcc understands -c and -o together... yes
checking how to run the C preprocessor... gcc -E
checking for grep that handles long lines and -e... /bin/grep
checking for egrep... /bin/grep -E
checking for ANSI C header files... yes
checking for sys/types.h... yes
checking for sys/stat.h... yes
checking for stdlib.h... yes
checking for string.h..

checking for double _Complex... yes
checking for long double _Complex... yes
checking for intptr_t... yes
checking for uintptr_t... yes
checking for mode_t... yes
checking for ssize_t... yes
checking for ptrdiff_t... yes
checking size of _Bool... 1
checking size of char... 1
checking size of short... 2
checking size of int... 4
checking size of long... 8
checking size of long long... 8
checking size of float... 4
checking size of double... 8
checking size of long double... 16
checking size of __float128... 16
checking size of float _Complex... 8
checking size of double _Complex... 16
checking size of long double _Complex... 32
checking size of void *... 8
checking size of size_t... 8
checking size of ssize_t... 8
checking size of ptrdiff_t... 8
checking size of wchar_t... 4
checking size of pid_t... 4
checking alignment of bool... 1
checking alignment of int8_t... 1
checking alignment of int16_t... 2
checking alignment of int32_t... 4
checking alignment of int64_t... 8
checking alignme

...

0 upgraded, 16 newly installed, 0 to remove and 121 not upgraded.
Need to get 39.5 MB of archives.
After this operation, 169 MB of additional disk space will be used.
Get:1 http://archive.ubuntu.com/ubuntu xenial-updates/main amd64 libpython2.7-minimal amd64 2.7.12-1ubuntu0~16.04.9 [338 kB]
Get:2 http://archive.ubuntu.com/ubuntu xenial-updates/main amd64 python2.7-minimal amd64 2.7.12-1ubuntu0~16.04.9 [1262 kB]
Get:3 http://archive.ubuntu.com/ubuntu xenial-updates/main amd64 python-minimal amd64 2.7.12-1~16.04 [28.1 kB]
Get:4 http://archive.ubuntu.com/ubuntu xenial-updates/main amd64 libpython2.7-stdlib amd64 2.7.12-1ubuntu0~16.04.9 [1884 kB]
Get:5 http://archive.ubuntu.com/ubuntu xenial-updates/main amd64 python2.7 amd64 2.7.12-1ubuntu0~16.04.9 [224 kB]
Get:6 http://archive.ubuntu.com/ubuntu xenial-updates/main amd64 libpython-stdlib amd64 2.7.12-1~16.04 [7768 B]
Get:7 http://archive.ubuntu.com/ubuntu xenial-updates/main amd64 python amd64 2.7.12-1~16.04 [137 kB]
Get:8 http://archive.

Get:5 http://ppa.launchpad.net/deadsnakes/ppa/ubuntu xenial/main amd64 libpython3.6-stdlib amd64 3.6.10-1+xenial1 [2217 kB]
Get:6 http://ppa.launchpad.net/deadsnakes/ppa/ubuntu xenial/main amd64 python3.6-minimal amd64 3.6.10-1+xenial1 [1713 kB]
Get:7 http://ppa.launchpad.net/deadsnakes/ppa/ubuntu xenial/main amd64 libpython3.6-minimal amd64 3.6.10-1+xenial1 [579 kB]
debconf: delaying package configuration, since apt-utils is not installed
Fetched 10.9 MB in 10s (1031 kB/s)
(Reading database ... 38128 files and directories currently installed.)
Preparing to unpack .../python3.6-dev_3.6.10-1+xenial1_amd64.deb ...
Unpacking python3.6-dev (3.6.10-1+xenial1) over (3.6.7-1+xenial1) ...
Preparing to unpack .../libpython3.6-dev_3.6.10-1+xenial1_amd64.deb ...
Unpacking libpython3.6-dev:amd64 (3.6.10-1+xenial1) over (3.6.7-1+xenial1) ...
Preparing to unpack .../libpython3.6_3.6.10-1+xenial1_amd64.deb ...
Unpacking libpython3.6:amd64 (3.6.10-1+xenial1) over (3.6.7-1+xenial1) ...
Preparing to unp

4 upgraded, 22 newly installed, 0 to remove and 110 not upgraded.
Need to get 47.4 MB of archives.
After this operation, 78.3 MB of additional disk space will be used.
Get:1 http://archive.ubuntu.com/ubuntu xenial-updates/main amd64 python3.5 amd64 3.5.2-2ubuntu0~16.04.9 [165 kB]
Get:2 http://archive.ubuntu.com/ubuntu xenial-updates/main amd64 libpython3.5-stdlib amd64 3.5.2-2ubuntu0~16.04.9 [2137 kB]
Get:3 http://archive.ubuntu.com/ubuntu xenial-updates/main amd64 python3.5-minimal amd64 3.5.2-2ubuntu0~16.04.9 [1593 kB]
Get:4 http://archive.ubuntu.com/ubuntu xenial-updates/main amd64 libpython3.5-minimal amd64 3.5.2-2ubuntu0~16.04.9 [524 kB]
Get:5 http://archive.ubuntu.com/ubuntu xenial-updates/main amd64 libmagic1 amd64 1:5.25-2ubuntu1.3 [216 kB]
Get:6 http://archive.ubuntu.com/ubuntu xenial-updates/main amd64 file amd64 1:5.25-2ubuntu1.3 [21.3 kB]
Get:7 http://archive.ubuntu.com/ubuntu xenial/main amd64 autotools-dev all 20150820.1 [39.8 kB]
Get:8 http://archive.ubuntu.com/ubuntu xe

Setting up libibverbs-dev (1.1.8-1.1ubuntu2) ...
Setting up libopenmpi-dev (1.10.2-8ubuntu1) ...
update-alternatives: using /usr/lib/openmpi/include to provide /usr/include/mpi (mpi) in auto mode
Processing triggers for libc-bin (2.23-0ubuntu10) ...
Removing intermediate container 969354a17b77
 ---> b09986c60671
Step 37/41 : ENV BASELINES_PATH /opt/baselines/
 ---> Running in b61185b0dfd8
Removing intermediate container b61185b0dfd8
 ---> 00a534ccc139
Step 38/41 : RUN git clone https://github.com/openai/baselines.git
 ---> Running in 324db80ffe2f
Cloning into 'baselines'...
Removing intermediate container 324db80ffe2f
 ---> effacfb13c0e
Step 39/41 : RUN pip install -e ${BASELINES_PATH}
 ---> Running in 7e442d0df9af
Obtaining file:///opt/baselines
  Created wheel for gym: filename=gym-0.15.7-py3-none-any.whl size=1648839 sha256=5c3edcc4d512b3028c24b7cd001ab6da1318e8a6bb72ed4213473b11c9f09979
  Stored in directory: /root/.cache/pip/wheels/05/39/c5/b2d60104a672c2fdafdf32c9c2937969c02eba99

f6e8fcde20d6: Pushed
a1897e4e88e5: Pushed
7a8e443a7521: Pushed
77047548c31d: Pushed
4e6dbc77826d: Pushed
e7c5a3d0576b: Pushed
7f83d475cf12: Pushed
640473ea059c: Pushed
c72ae9f5e6f3: Pushed
6b14198ed87a: Pushed
ac290905e689: Pushed
b38125267a5f: Pushed
50c820514472: Pushed
e7a63544b256: Pushed
a4240cb88ca2: Pushed
474778358c2a: Pushed
41db321cb494: Pushed
dce654228692: Pushed
4b8591ba9ec9: Pushed
ca3c107e6e73: Pushed
f2800c73caf0: Pushed
c4d1fd31e806: Pushed
b8450e6ea80e: Pushed
0a789d5934c5: Pushed
b78a18cd8c7b: Pushed
190521d0374f: Pushed
20390fc7ce8b: Pushed
8dc697f100a6: Pushed
e27149f08c66: Pushed
d6df154a329b: Pushed
77ece2928bd0: Pushed
6ee8fe30b55b: Pushed
60a4c6264060: Pushed
36cb14e2633d: Pushed
70b9dbc01d26: Pushed
c9bbcdfaaa98: Pushed
302af95b9e68: Pushed
1f54e44d071b: Pushed
0ecacb4d5bb1: Pushed
d6db7d05e3b2: Pushed
a0f6963b385e: Pushed
3db5746c911a: Pushed
819a824caf70: Pushed
647265b9d8bc: Pushed
8d999119430c: Pushed
fe4ed9a0e78a: Pushed
41c002c8a6fd: Pushed
09b011f6bf18:

## 훈련 코드 작성

#### RL 알고리즘에 대한 사전 설정 구성

RL 훈련 작업을 구성하는 사전 설정(preset)은 `./src` 디렉토리의 `preset-half-cheetah.py`에 정의되어 있습니다. 사전 설정 파일을 사용하여 에이전트 파라메터들을 정의하여 특정 에이전트 알고리즘을 선택할 수 있습니다. 환경 파라메터를 설정하고, 스케줄 및 시각화 파라메터를 정의하고, 그래프 관리자를 정의 할 수도 있습니다. 스케줄 사전 설정은 PPO1 알고리즘 훈련을 위해 다음과 같은 하이퍼파라미터들을 정의합니다.

* `num_timesteps`: (int) 훈련 스텝 수 - 사전 설정: 1e4
* `timesteps_per_actorbatch` – (int) 업데이트 당 액터 당 타입스텝 - 사전 설정: 2048
* `clip_param` – (float) clipping 파라메터 epsilon - 사전 설정: 0.2
* `entcoeff` – (float) entropy loss weight - 사전 설정: 0.0
* `optim_epochs` – (float) 옵티마이저의 에포크(epoch) 수 - 사전 설정: 10
* `optim_stepsize` – (float) 옵티마이저의 스텝 크기 - 사전 설정: 3e-4
* `optim_batchsize` – (int) 옵티마이저의 배치 크기 - 사전 설정: 64
* `gamma` – (float) 감가율(discount factor) - 사전 설정: 0.99
* `lam` – (float) advantage 추정 - 사전 설정: 0.95
* `schedule` – (str) 학습률 업데이트를 위한 스케줄러 유형 (‘linear’, ‘constant’, ‘double_linear_con’, ‘middle_drop’ 또는 ‘double_middle_drop’) - 사전 설정: linear
* `verbose` – (int) verbosity 수준: 0 없음, 1 훈련 정보, 2 tensorflow 디버그 - 사전 설정: 1

여러분은 https://stable-baselines.readthedocs.io/en/master/modules/ppo1.html 에서 PPO1 알고리즘에 대한 전체 인수 및 문서 목록을 참조할 수 있습니다.

`RLSTABLEBASELINES_PRESET` 하이퍼파라미터를 지정하여 런타임 시, 이를 오버라이드할 수 있습니다. 또한 사용자 정의 하이퍼파라미터를 정의하는 데 사용할 수 있습니다.

In [9]:
!pygmentize src/preset-{roboschool_problem}.py

import argparse

from sagemaker_rl.stable_baselines_launcher import SagemakerStableBaselinesPPO1Launcher, create_env


def parse_args():
    parser = argparse.ArgumentParser()
    parser.add_argument('--output_path', default="/opt/ml/output/intermediate/", type=str)
    parser.add_argument('--num_timesteps', default=1e4)
    parser.add_argument('--timesteps_per_actorbatch', default=2048, type=int)
    parser.add_argument('--clip_param', default=0.2, type=float)
    parser.add_argument('--entcoeff', default=0.0, type=float)
    parser.add_argument('--optim_epochs', default=10, type=int)
    parser.add_argument('--optim_stepsize', default=3e-4)
    parser.add_argument('--optim_batchsize', default=64, type=int)
    parser.add_argument('--gamma', default=0.99, type=float)
    parser.add_argument('--lam', default=0.95, type=float)
    parser.add_argument('--schedule', default="linear", type=str)
    parser.add_argument('--verbose', default=1, type=int)

    return parser.parse_known_args()


#### Write the Training Code

The training code is in the file `train-coach.py` which is also the `./src` directory.

In [10]:
!pygmentize src/train_stable_baselines.py

import argparse

from sagemaker_rl.mpi_launcher import MPILauncher


def parse_args():
    parser = argparse.ArgumentParser()
    parser.add_argument('--RLSTABLEBASELINES_PRESET', required=True, type=str)
    parser.add_argument('--output_path', default="/opt/ml/output/intermediate/", type=str)
    parser.add_argument('--instance_type', type=str)

    return parser.parse_known_args()


if __name__ == "__main__":
    args, unknown_args = parse_args()
    print("Launching train script with MPI: {} and arguments: {}".format(args.RLSTABLEBASELINES_PRESET,
                                                                         str(unknown_args)))
    MPILauncher(train_script=args.RLSTABLEBASELINES_PRESET, train_script_args=unknown_args,
                instance_type=args.instance_type).mpi_run()


## Python SDK 스크립트 모드를 사용하여 RL 모델 훈련

로컬 모드를 사용하는 경우 노트북 인스턴스에서 훈련이 실행됩니다. 훈련을 위해 SageMaker를 사용할 때 GPU 또는 CPU 인스턴스를 선택할 수 있습니다. RLEstimator는 RL 작업 훈련에 사용됩니다.

1. 환경, 사전 설정 및 교육 코드가 업로드되는 소스 디렉토리를 지정합니다.
2. 엔트리 포인트(entry point)를 훈련 코드로 지정합니다.
3. RL 툴킷 및 프레임 워크를 선택합니다. 이는 RL 컨테이너의 ECR 경로로 자동 확인됩니다.
4. 인스턴스 수, 작업 이름(job name), 출력에 대한 S3 경로 및 작업 이름과 같은 훈련 파라메터들을 정의합니다.
5. RL 에이전트 알고리즘의 하이퍼파라미터를 지정합니다. `RLSTABLEBASELINES_PRESET`을 사용하여 사용하려는 RL 에이전트 알고리즘을 지정할 수 있습니다.
6. 여러분의 로그에서 캡처할 지표(metric)를 정의합니다. CloudWatch 및 SageMaker Notebook에서도 시각화할 수 있습니다.

`preset-half-cheetah.py`에 구성된 모든 사전 설정 파라메터는 `hyperparameters` 블록에 재정의 값을 지정하여 재정의 할 수 있습니다.

**참고** : MPI 기반 작업의 경우 로컬 모드는 단일 인스턴스 작업에서만 지원됩니다. 로컬 모드를 사용하는 경우 `instance_type`을 `1`로 사용하세요.

In [19]:
%%time

estimator = RLEstimator(entry_point="train_stable_baselines.py",
                        source_dir='src',
                        dependencies=["common/sagemaker_rl"],
                        image_name=custom_image_name,
                        role=role,
                        train_instance_type=instance_type,
                        train_instance_count=10,
                        output_path=s3_output_path,
                        base_job_name=job_name_prefix,
                        hyperparameters={
                            "RLSTABLEBASELINES_PRESET":"preset-{}.py".format(roboschool_problem),
                            "num_timesteps":1e5,
                            "instance_type":instance_type
                        },
                        metric_definitions= [
                            {
                                "Name":"EpisodesLengthMean",
                                "Regex":"\[.*,.*\]\<stdout\>\:\| *EpLenMean *\| *([-+]?[0-9]*\.?[0-9]*) *\|"
                            },
                            {
                                "Name":"EpisodesRewardMean",
                                "Regex":"\[.*,.*\]\<stdout\>\:\| *EpRewMean *\| *([-+]?[0-9]*\.?[0-9]*) *\|"
                            },
                            {
                                "Name":"EpisodesSoFar",
                                "Regex":"\[.*,.*\]\<stdout\>\:\| *EpisodesSoFar *\| *([-+]?[0-9]*\.?[0-9]*) *\|"
                            }
                        ]
                    )

estimator.fit(wait=True)

2020-03-28 14:48:39 Starting - Starting the training job...
2020-03-28 14:48:58 Starting - Launching requested ML instances......
2020-03-28 14:50:05 Starting - Preparing the instances for training.........
2020-03-28 14:51:28 Downloading - Downloading input data
2020-03-28 14:51:28 Training - Downloading the training image.........
2020-03-28 14:53:03 Training - Training image download completed. Training in progress.bash: cannot set terminal process group (-1): Inappropriate ioctl for device
bash: no job control in this shell
2020-03-28 14:52:58,055 sagemaker-containers INFO     Imported framework sagemaker_tensorflow_container.training
2020-03-28 14:52:58,058 sagemaker-containers INFO     No GPUs detected (normal if no gpus installed)
2020-03-28 14:52:58,193 sagemaker-containers INFO     No GPUs detected (normal if no gpus installed)
2020-03-28 14:52:58,206 sagemaker-containers INFO     Invoking user script

Training Env:

{
    "additional_framework_parameters": {
        "sagemake

bash: cannot set terminal process group (-1): Inappropriate ioctl for device
bash: no job control in this shell
2020-03-28 14:53:04,489 sagemaker-containers INFO     Imported framework sagemaker_tensorflow_container.training
2020-03-28 14:53:04,493 sagemaker-containers INFO     No GPUs detected (normal if no gpus installed)
2020-03-28 14:53:04,624 sagemaker-containers INFO     No GPUs detected (normal if no gpus installed)
2020-03-28 14:53:04,638 sagemaker-containers INFO     Invoking user script

Training Env:

{
    "additional_framework_parameters": {
        "sagemaker_estimator": "RLEstimator"
    },
    "channel_input_dirs": {},
    "current_host": "algo-2",
    "framework_module": "sagemaker_tensorflow_container.training:main",
    "hosts": [
        "algo-1",
        "algo-2",
        "algo-3",
        "algo-4",
        "algo-5",
        "algo-6",
        "algo-7",
        "algo-8",
        "algo-9",
        "algo-10"
    ],
    "hyperparameters": {
        "num_timesteps": 100

[1,3]<stdout>:Starting training for half cheetah with PPO1
[1,2]<stdout>:Starting training for half cheetah with PPO1
[1,3]<stdout>:Launching training script with stable baselines PPO1
[1,2]<stdout>:Launching training script with stable baselines PPO1
[1,0]<stdout>:Starting training for half cheetah with PPO1
[1,4]<stdout>:Starting training for half cheetah with PPO1
[1,7]<stdout>:Starting training for half cheetah with PPO1
[1,0]<stdout>:Launching training script with stable baselines PPO1
[1,5]<stdout>:Starting training for half cheetah with PPO1
[1,7]<stdout>:Launching training script with stable baselines PPO1
[1,9]<stdout>:Starting training for half cheetah with PPO1
[1,4]<stdout>:Launching training script with stable baselines PPO1
[1,5]<stdout>:Launching training script with stable baselines PPO1
[1,9]<stdout>:Launching training script with stable baselines PPO1
[1,1]<stdout>:Starting training for half cheetah with PPO1
[1,1]<stdout>:Launching training script with stable baselin

[1,5]<stdout>:Optimizing...
[1,5]<stdout>:     pol_surr |    pol_entpen |       vf_loss |            kl |           ent
[1,0]<stdout>:Optimizing...
[1,0]<stdout>:     pol_surr |    pol_entpen |       vf_loss |            kl |           ent
[1,7]<stdout>:Optimizing...
[1,7]<stdout>:     pol_surr |    pol_entpen |       vf_loss |            kl |           ent
[1,2]<stdout>:Optimizing...
[1,2]<stdout>:     pol_surr |    pol_entpen |       vf_loss |            kl |           ent
[1,6]<stdout>:Optimizing...
[1,6]<stdout>:     pol_surr |    pol_entpen |       vf_loss |            kl |           ent
[1,8]<stdout>:Optimizing...
[1,8]<stdout>:     pol_surr |    pol_entpen |       vf_loss |            kl |           ent
[1,3]<stdout>:Optimizing...
[1,3]<stdout>:     pol_surr |    pol_entpen |       vf_loss |            kl |           ent
[1,4]<stdout>:Optimizing...
[1,4]<stdout>:     pol_surr |    pol_entpen |       vf_loss |            kl |           ent
[1,1]<stdout>:Optimizing...
[1,1]<stdout

[1,5]<stdout>:Optimizing...
[1,5]<stdout>:     pol_surr |    pol_entpen |       vf_loss |            kl |           ent
[1,0]<stdout>:Optimizing...
[1,0]<stdout>:     pol_surr |    pol_entpen |       vf_loss |            kl |           ent
[1,6]<stdout>:Optimizing...
[1,6]<stdout>:     pol_surr |    pol_entpen |       vf_loss |            kl |           ent
[1,2]<stdout>:Optimizing...
[1,2]<stdout>:     pol_surr |    pol_entpen |       vf_loss |            kl |           ent
[1,3]<stdout>:Optimizing...
[1,3]<stdout>:     pol_surr |    pol_entpen |       vf_loss |            kl |           ent
[1,7]<stdout>:Optimizing...
[1,7]<stdout>:     pol_surr |    pol_entpen |       vf_loss |            kl |           ent
[1,8]<stdout>:Optimizing...
[1,8]<stdout>:     pol_surr |    pol_entpen |       vf_loss |            kl |           ent
[1,1]<stdout>:Optimizing...
[1,1]<stdout>:     pol_surr |    pol_entpen |       vf_loss |            kl |           ent
[1,4]<stdout>:Optimizing...
[1,4]<stdout


2020-03-28 14:54:42 Uploading - Uploading generated training model2020-03-28 14:54:37,969 sagemaker-containers INFO     Reporting training SUCCESS
Training process started by MPI on worker node %s stopped algo-10
2020-03-28 14:54:39,549 sagemaker-containers INFO     Reporting training SUCCESS
Training process started by MPI on worker node %s stopped algo-8
2020-03-28 14:54:40,130 sagemaker-containers INFO     Reporting training SUCCESS
Training process started by MPI on worker node %s stopped algo-7
2020-03-28 14:54:40,122 sagemaker-containers INFO     Reporting training SUCCESS
Training process started by MPI on worker node %s stopped algo-9
2020-03-28 14:54:39,834 sagemaker-containers INFO     Reporting training SUCCESS
Training process started by MPI on worker node %s stopped algo-2
2020-03-28 14:54:40,242 sagemaker-containers INFO     Reporting training SUCCESS
Training process started by MPI on worker node %s stopped algo-3
2020-03-28 14:54:40,374 sagemaker-containers INFO     Re

## 시각화

RL 훈련에는 시간이 오래 걸릴 수 있습니다. 따라서 훈련 작업이 동작하는 동안 훈련 작업의 진행 상황을 추적할 수 있는 다양한 방법들이 있습니다. 훈련 도중 일부 중간 출력이 S3에 저장되므로, 이를 캡처하도록 설정합니다.

### 훈련 롤아웃 비디오 가져오기

특정 롤아웃의 비디오는 훈련 중 S3에 기록됩니다. 여기서 우리는 사용 가능한 모든 비디오 클립을 가져오고 마지막 비디오를 렌더링합니다.

In [20]:
job_name = estimator.latest_training_job.job_name
print("Training job: %s" % job_name)

s3_url = "s3://{}/{}".format(s3_bucket,job_name)

if local_mode:
    output_tar_key = "{}/output.tar.gz".format(job_name)
else:
    output_tar_key = "{}/output/output.tar.gz".format(job_name)

intermediate_folder_key = "{}/output/intermediate".format(job_name)
output_url = "s3://{}/{}".format(s3_bucket, output_tar_key)
intermediate_url = "s3://{}/{}".format(s3_bucket, intermediate_folder_key)

print("S3 job path: {}".format(s3_url))
print("Output.tar.gz location: {}".format(output_url))
print("Intermediate folder path: {}".format(intermediate_url))
    
tmp_dir = "/tmp/{}".format(job_name)
os.system("mkdir {}".format(tmp_dir))
print("Create local folder {}".format(tmp_dir))
wait_for_s3_object(s3_bucket, intermediate_folder_key, tmp_dir) 

Training job: rl-roboschool-half-cheetah-2020-03-28-14-48-39-428
S3 job path: s3://sagemaker-us-west-2-143656149352/rl-roboschool-half-cheetah-2020-03-28-14-48-39-428
Output.tar.gz location: s3://sagemaker-us-west-2-143656149352/rl-roboschool-half-cheetah-2020-03-28-14-48-39-428/output/output.tar.gz
Intermediate folder path: s3://sagemaker-us-west-2-143656149352/rl-roboschool-half-cheetah-2020-03-28-14-48-39-428/output/intermediate
Create local folder /tmp/rl-roboschool-half-cheetah-2020-03-28-14-48-39-428
Waiting for s3://sagemaker-us-west-2-143656149352/rl-roboschool-half-cheetah-2020-03-28-14-48-39-428/output/intermediate...


['/tmp/rl-roboschool-half-cheetah-2020-03-28-14-48-39-428/0.monitor.csv',
 '/tmp/rl-roboschool-half-cheetah-2020-03-28-14-48-39-428/1.monitor.csv',
 '/tmp/rl-roboschool-half-cheetah-2020-03-28-14-48-39-428/2.monitor.csv',
 '/tmp/rl-roboschool-half-cheetah-2020-03-28-14-48-39-428/3.monitor.csv',
 '/tmp/rl-roboschool-half-cheetah-2020-03-28-14-48-39-428/4.monitor.csv',
 '/tmp/rl-roboschool-half-cheetah-2020-03-28-14-48-39-428/5.monitor.csv',
 '/tmp/rl-roboschool-half-cheetah-2020-03-28-14-48-39-428/6.monitor.csv',
 '/tmp/rl-roboschool-half-cheetah-2020-03-28-14-48-39-428/7.monitor.csv',
 '/tmp/rl-roboschool-half-cheetah-2020-03-28-14-48-39-428/8.monitor.csv',
 '/tmp/rl-roboschool-half-cheetah-2020-03-28-14-48-39-428/9.monitor.csv',
 '/tmp/rl-roboschool-half-cheetah-2020-03-28-14-48-39-428/rl_out.meta.json',
 '/tmp/rl-roboschool-half-cheetah-2020-03-28-14-48-39-428/rl_out.mp4']

### RL 출력 비디오

In [21]:
import io
import base64
video = io.open("{}/rl_out.mp4".format(tmp_dir), 'r+b').read()
encoded = base64.b64encode(video)
HTML(data='''<video alt="test" controls>
                <source src="data:video/mp4;base64,{0}" type="video/mp4" />
             </video>'''.format(encoded.decode('ascii')))

### 학습된  HalfCheetah의 걷기 예시

다음과 같은 추가 구성으로 훈련 작업을 수행 후, 아래 비디오 클립과 같은 결과를 확인할 수 있습니다.
* `train_instance_count`: 10
* `train_instance_type`: ml.c4.xlarge
* `num_timesteps`: 1e7

위의 설정으로 모델을 훈련하는 데 약 40분이 소요됩니다. 저렴한 인스턴스와 더 많은 훈련 기간으로 유사한 결과를 얻을 수 있습니다.

In [18]:
import io
import base64
video = io.open("examples/robo_half_cheetah_10x_40min.mp4", 'r+b').read()
encoded = base64.b64encode(video)
HTML(data='''<video alt="test" controls>
                <source src="data:video/mp4;base64,{0}" type="video/mp4" />
             </video>'''.format(encoded.decode('ascii')))